# TP3: Arithmétique et cryptographie

## 1. Arithmétique modulaire

1. Construisez la table d'addition et de multiplication des entiers modulo 5. Pour une présentation plus agréable, considérez la fonction `Matrix` comme dans le TP 2

In [7]:
from sympy import *
import sympy as sy

In [10]:
 # pour l'addition
x,y = symbols(['x','y'])
Matrix(5,5, Lambda([x,y],(x+y)%5))

# ou : 
Matrix ([[(i+j)%5 for j in range(5)] for i in range(5)])

Matrix([
[0, 1, 2, 3, 4],
[1, 2, 3, 4, 0],
[2, 3, 4, 0, 1],
[3, 4, 0, 1, 2],
[4, 0, 1, 2, 3]])

In [11]:
 # pour la multiplication
Matrix(5,5, Lambda([x,y],(x*y)%5))

 # ou : 
Matrix ([[(i*j)%5 for j in range(5)] for i in range(5)])

Matrix([
[0, 0, 0, 0, 0],
[0, 1, 2, 3, 4],
[0, 2, 4, 1, 3],
[0, 3, 1, 4, 2],
[0, 4, 3, 2, 1]])

2. Ecrivez une fonction `CoprimeQ` qui prend en entrée deux entiers et qui renvoie `True` si les entiers sont premiers entre eux

In [14]:
def CoprimeQ(n,m) :
    return gcd(n,m)==1

In [15]:
CoprimeQ(3,11)

True

3. Programmez l'algorithme d'Euclide étendu itératif suivant et vérifiez qu'il fonctionne bien en comparant avec celui de la librairie `Sympy`. La fonction `floor` se trouve dans la librairie `math` mais corresond aussi à la division entière `//`. Les variables `Q` et `R` ne peuvent pas être des tuples (il n'y a pas d'arithmétique des tuples).

In [25]:
def euclideEtendu(q,r) : 
    if q>=r: raise Exception("q >= r")
    Q = (1,0)
    R = (0,1)
    while r!=0 :
        t = q%r 
        T = (Q[0] - (q//r)*R[0], Q[1] - (q//r)*R[1])
        print(q,r,t,Q,(q//r),R,T)
        q,r = r,t 
        Q,R = R,T
    return(Q,q)

In [26]:
euclideEtendu(11,26)

11 26 11 (1, 0) 0 (0, 1) (1, 0)
26 11 4 (0, 1) 2 (1, 0) (-2, 1)
11 4 3 (1, 0) 2 (-2, 1) (5, -2)
4 3 1 (-2, 1) 1 (5, -2) (-7, 3)
3 1 0 (5, -2) 3 (-7, 3) (26, -11)


((-7, 3), 1)

In [18]:
gcdex(11,26)

(-7, 3, 1)

Pour comprendre le fonctionnement, remplissez le tableau qui trace les valeurs de `q,r,t,Q,floor(q/r),R,T`. ![](EucEt1126.png)

4. Ecrivez une fonction `modinv` qui prend en entrée `a` et `m` et qui renvoie l'inverse de `a`modulo `m` s'il existe et retourne une erreur sinon

In [21]:
def modinv(a,m) :
    if gcd(a,m) == 1 : 
        return gcdex(a,m)[0]
    else :
        if d%b !=0: 
            raise Exception("pas d'inverse")
        else : 
            return gcd(a,m)*modinv((a/gcd(a,m)), (m/gcd(a,m)))

In [22]:
modinv(3,26)

9

5. Reprenez le code de l'exponentielle modulaire $a^b\mod n$ et instrumentez le code pour faire la trace d'exécution en remplissant un tableau comme dans l'exemple ![](exponentMod.png)

In [24]:
def exponentMod(a,b,p):
    res=1
    loop = 0
    for i in bin(b)[2:]:
        res=(res*res)%p
        if i=='1':
            res=(res*a)%p
        print(loop, i,res**2,res)
        loop += 1
    return(res)

exponentMod(17,73,100)

0 1 289 17
1 0 7921 89
2 0 441 21
3 1 9409 97
4 0 81 9
5 0 6561 81
6 1 1369 37


37

## 2. RSA

1. Ecrivez une fonction `genCle` qui prend en entrée une taille (celle de la clé) exprimée en octets (1 octet = 8 bits) et qui retourne le tuple composé de l'entier $p$ et de l'entier $q$.

In [27]:
def genCle(t):
    size = 2**(8*t)
    p = prevprime(size)
    q = prevprime(p)
    return(p,q)

In [28]:
genCle(4)

(4294967291, 4294967279)

2. Ecrivez les fonctions `clePub` et `clePriv` qui ont un fonctionnement analogue à `rsa_public_key` et `rsa_private_key`. N'oubliez pas de fournir la valeur de `e`.

In [29]:
def clePub(p,q,e):
    return (p*q,e)

def clePriv(p,q,e):
    n=p*q
    phi=(p-1)*(q-1)
    d= modinv(e,phi)
    cle=(n,d)
    return cle

3. Ecrivez une fonction `RSA`en `Python` qui prend en entrée :
    - soit la clé publique: le tuple $(n,e)$ et un entier $m$ et qui renvoie $m^e\mod n$
    - soit la clé privée: le tuple $(n,d)$ et un entier $c$ et qui renvoie $c^d\mod n$

In [32]:
def rsa(m,cle):
    return pow(m,cle[1],cle[0])

In [33]:
rsa(3,(509,11))

15

4. Utilisez votre fonction `RSA` pour construire `RSAEnc` et `RDADec` dont le comportement est analogue à `encipher_rsa(m,pk)` et `decipher_rsa(c,dk)` de l'implémentation RSA de `Sympy`.

In [34]:
def RSAEnc(m,pub):
    return rsa(m,pub)

In [35]:
RSAEnc(3,(509*521,11))

177147

In [36]:
def RSADec(c,priv):
    return rsa(c,priv)

In [37]:
RSADec(177147,(509*521,216131))

3

5. En utilisant les fonctions de codage et de décodage du cours, tarnsformez les fonctions `RSAEnc` et `RSADec` pour qu'elles pemettent de chiffrer et de déchiffer des chaines de caractères.

In [ ]:
DEFAULT_BLOCK_SIZE = 128 # taille bloc doit être inférieure à la taille de la clé et elle est en octets 
BYTE_SIZE=256 # un octet a 2**8=256 valeurs possibles


def Text2Ints(message,blockSize=DEFAULT_BLOCK_SIZE):
    # convertit une chaine en une liste de blocs d'entiers.    
    # chaque entier représente 'blockSize' caractères de la chaîne    
    messageBytes=message.encode('ascii')   
    # convertit la chaine en octets    
    blockInts=[]                           
    # initialise la liste de s entiers    
    for blockStart in range(0,len(messageBytes),blockSize):       
        # calculer l'entier correspondant au bloc de texte        
        blockInt=0        
        for i in range(blockStart,min(blockStart+blockSize,len(messageBytes))):            
            blockInt += int(messageBytes[i])*(BYTE_SIZE ** (i%blockSize))        
        blockInts.append(blockInt)    
    return blockInts


def Ints2Text(blockInts,messageLength,blockSize=DEFAULT_BLOCK_SIZE) :
    # convertit une liste de blocs d'entiers et retourne la chaine correspondante.    
    # on a besoin de la longueur du message passée dans messageLeng th pour convertir     
    # le dernier bloc d'entier    
    message=[]    
    for blockInt in blockInts:         
        blockMessage=[]         
        # initialise la liste qui contiendr a les caractères        
        for i in range(blockSize-1,-1,-1):            
            if len(message)+i < messageLength:                
                # décode la chaine des 'blockSize' caractères depui s ce bloc d'entier                
                charNumber=blockInt//(BYTE_SIZE**i)                
                # on passe au bloc suivant                
                blockInt=blockInt%(BYTE_SIZE**i)                
                blockMessage.insert(0,bytes([charNumber]).decode('a scii'))        
        message.extend(blockMessage)    
    return ''.join(message)

In [ ]:
def RSAEncMessage(message,pub):
    m=Text2Ints(message)
    crypt=""
    for block in m:
        crypt=crypt+Ints2Text(RSAEnc(block,pub))
    return crypt

def RSADecMessage(crypt,priv):
    crypt=Text2Ints(message)
    message=""
    for block in crypt:
        message=message+Ints2Text(RSAEnc(block,priv))
    return message 